In [0]:
from pyspark.sql import functions as F, types as T
from pyspark.sql.window import Window
from delta.tables import DeltaTable
from pyspark.sql import DataFrame, SparkSession
from pyspark.sql.types import *
from functools import reduce

#Functions

In [0]:
def write_to_table(
    df: DataFrame,
    table_name: str,
    mode: str = "overwrite",
    merge_schema: bool = False,
    partition_by: list[str] = None,
    path: str = None,
    save_as_table: bool = True
) -> None:
    """
    Generalised Delta write helper for bronze layer.

    Parameters:
    - df (DataFrame): Spark DataFrame to write.
    - table_name (str): Name of the Delta table (used if save_as_table=True).
    - mode (str): Write mode ('overwrite', 'append', 'ignore', 'error', etc.).
    - merge_schema (bool): Whether to merge schema on write.
    - partition_by (list[str], optional): List of columns to partition by.
    - path (str, optional): Path to save the Delta table (used if save_as_table=False).
    - save_as_table (bool): If True, saves as managed table; else saves to path.

    Raises:
    - ValueError: If neither save_as_table nor path is properly specified.
    """

    df_with_ts = df.withColumn("last_updated", F.current_timestamp())

    writer = df_with_ts.write.format("delta").mode(mode)

    if merge_schema:
        writer = writer.option("mergeSchema", "true")
    elif mode == "overwrite":
        writer = writer.option("overwriteSchema", "true")

    if partition_by:
        writer = writer.partitionBy(*partition_by)

    if save_as_table:
        writer.saveAsTable(table_name)
    elif path:
        writer.save(path)
    else:
        raise ValueError("Either save_as_table must be True or a path must be provided.")

#Variables

In [0]:
try:
    ENV = dbutils.widgets.get("ENV")
except Exception:
    ENV = "dev"

try:
    PROTOCOL = dbutils.widgets.get("PROTOCOL")
except Exception:
    PROTOCOL = "HIST"

#ensure valid ENV and PROTOCOL
valid_envs = {"dev", "test", "prod"}
valid_protocols = {"HIST", "INCR"}

# Validate ENV
if ENV not in valid_envs:
    print(f"Invalid ENV: {ENV}. Must be one of {valid_envs}. Exiting notebook.")
    dbutils.notebook.exit("Invalid ENV")

# Validate PROTOCOL
if PROTOCOL not in valid_protocols:
    print(f"Invalid PROTOCOL: {PROTOCOL}. Must be one of {valid_protocols}. Exiting notebook.")
    dbutils.notebook.exit("Invalid PROTOCOL")
    
silver_schema = f"fpl_silver_{ENV}"
feature_schema = f"fpl_feature_{ENV}"
rolling_window_size = 5 

#Load Source Tables

In [0]:
fixtures_df = spark.table(f"{silver_schema}.fixtures").filter(F.col("home_team_score").isNotNull())
teams_df = spark.table(f"{silver_schema}.teams")
stats_df = spark.table(f"{silver_schema}.gameweek_stats")

#Team Feature Engineering

In [0]:
#Step 1: Aggregate xG, xA, and exp_stats_available per team per fixture
team_xg_xa_df = (
    stats_df.groupBy("fixture_key", "team_key")
    .agg(
        F.sum("expected_goals").alias("team_expected_goals"),
        F.sum("expected_assists").alias("team_expected_assists"),
        F.max("exp_stats_available").alias("team_exp_stats_available")
    )
    .withColumn(
        "team_expected_goal_involvements",
        F.col("team_expected_goals") + F.col("team_expected_assists")
    )
)

#Create opponent xG/xA aggregates
opponent_xg_xa_df = (
    team_xg_xa_df.select(
        "fixture_key",
        F.col("team_key").alias("opponent_team_key"),
        F.col("team_expected_goals").alias("expected_goals_against"),
        F.col("team_expected_assists").alias("expected_assists_against"),
        F.col("team_expected_goal_involvements").alias("expected_goal_involvements_against")
    )
)

#Step 3: Transform fixtures into team-level records
home_df = (
    fixtures_df.select(
        "fixture_key",
        "season_key",
        "gameweek_key",
        F.col("home_team_key").alias("team_key"),
        F.col("away_team_key").alias("opponent_team_key"),
        F.lit(True).alias("is_home"),
        F.col("home_team_score").alias("goals_for"),
        F.col("away_team_score").alias("goals_against")
    )
)

away_df = (
    fixtures_df.select(
        "fixture_key",
        "season_key",
        "gameweek_key",
        F.col("away_team_key").alias("team_key"),
        F.col("home_team_key").alias("opponent_team_key"),
        F.lit(False).alias("is_home"),
        F.col("away_team_score").alias("goals_for"),
        F.col("home_team_score").alias("goals_against")
    )
)

team_fixtures_df = home_df.unionByName(away_df)

#Add match-level metrics using withColumns
team_fixtures_df = team_fixtures_df.withColumns({
    "goal_diff": F.col("goals_for") - F.col("goals_against"),
    "match_points": F.when(F.col("goals_for") > F.col("goals_against"), F.lit(3))
                    .when(F.col("goals_for") == F.col("goals_against"), F.lit(1))
                    .otherwise(F.lit(0))
})

#Join team xG/xA and opponent xG/xA
team_fixtures_df = (
    team_fixtures_df.join(team_xg_xa_df, on=["fixture_key", "team_key"], how="left")
    .join(opponent_xg_xa_df, on=["fixture_key", "opponent_team_key"], how="left")
)

#Compute rolling metrics using withColumns
rolling_window = Window.partitionBy("team_key", "season_key").orderBy("gameweek_key").rowsBetween(-rolling_window_size + 1, 0)

team_fixtures_df = team_fixtures_df.withColumns({
    "rolling_points": F.sum("match_points").over(rolling_window),
    "rolling_goal_diff": F.sum("goal_diff").over(rolling_window),
    "home_rolling_points": F.sum(F.when(F.col("is_home"), F.col("match_points")).otherwise(0)).over(rolling_window),
    "away_rolling_points": F.sum(F.when(~F.col("is_home"), F.col("match_points")).otherwise(0)).over(rolling_window),
    "rolling_team_expected_goals": F.sum("team_expected_goals").over(rolling_window),
    "rolling_team_expected_assists": F.sum("team_expected_assists").over(rolling_window),
    "rolling_team_expected_goal_involvements": F.sum("team_expected_goal_involvements").over(rolling_window),
    "rolling_expected_goals_against": F.sum("expected_goals_against").over(rolling_window),
    "rolling_expected_assists_against": F.sum("expected_assists_against").over(rolling_window),
    "rolling_expected_goal_involvements_against": F.sum("expected_goal_involvements_against").over(rolling_window),
    "rolling_goal_difference": F.sum("goal_diff").over(rolling_window),
    "rolling_games_played": F.count("fixture_key").over(rolling_window),
    "avg_team_expected_goals": F.round(F.col("rolling_team_expected_goals") / F.col("rolling_games_played"), 3),
    "avg_team_expected_assists": F.round(F.col("rolling_team_expected_assists") / F.col("rolling_games_played"), 3),
    "avg_team_expected_goal_involvements": F.round(F.col("rolling_team_expected_goal_involvements") / F.col("rolling_games_played"), 3),
    "avg_expected_goals_against": F.round(F.col("rolling_expected_goals_against") / F.col("rolling_games_played"), 3),
    "avg_expected_assists_against": F.round(F.col("rolling_expected_assists_against") / F.col("rolling_games_played"), 3),
    "avg_expected_goal_involvements_against": F.round(F.col("rolling_expected_goal_involvements_against") / F.col("rolling_games_played"), 3),
    "avg_goal_difference": F.round(F.col("rolling_goal_difference") / F.col("rolling_games_played"), 3)
})

#Join team metadata
team_features_df = team_fixtures_df.join(
    teams_df.select("team_key", "team_name", "team_name_short", "is_promoted", "is_relegated", "season_key"),
    on=["team_key", "season_key"],
    how="left"
)

#Select final columns
team_features_df = team_features_df.select(
    "team_key", "team_name", "team_name_short", "season_key", "gameweek_key",
    "is_home", "goals_for", "goals_against", "goal_diff", "match_points",
    "team_expected_goals", "team_expected_assists", "team_expected_goal_involvements",
    "expected_goals_against", "expected_assists_against", "expected_goal_involvements_against",
    "team_exp_stats_available",
    "rolling_points", "rolling_goal_diff", "home_rolling_points", "away_rolling_points",
    "rolling_team_expected_goals", "rolling_team_expected_assists", "rolling_team_expected_goal_involvements",
    "rolling_expected_goals_against", "rolling_expected_assists_against", "rolling_expected_goal_involvements_against",
    "rolling_goal_difference", "rolling_games_played",
    "avg_team_expected_goals", "avg_team_expected_assists", "avg_team_expected_goal_involvements",
    "avg_expected_goals_against", "avg_expected_assists_against", "avg_expected_goal_involvements_against",
    "avg_goal_difference",
    "is_promoted", "is_relegated"
)

write_to_table(
    df=team_features_df,
    table_name=f"{feature_schema}.team_features",
    mode="overwrite"
)

In [0]:
display(team_features_df)

team_key team_name team_name_short season_key gameweek_key is_home goals_for goals_against goal_diff match_points team_expected_goals team_expected_assists team_expected_goal_involvements expected_goals_against expected_assists_against expected_goal_involvements_against team_exp_stats_available rolling_points rolling_goal_diff home_rolling_points away_rolling_points rolling_team_expected_goals rolling_team_expected_assists rolling_team_expected_goal_involvements rolling_expected_goals_against rolling_expected_assists_against rolling_expected_goal_involvements_against rolling_goal_difference rolling_games_played avg_team_expected_goals avg_team_expected_assists avg_team_expected_goal_involvements avg_expected_goals_against avg_expected_assists_against avg_expected_goal_involvements_against avg_goal_difference is_promoted is_relegated 1 Manchester United MUN 201617 20161701 false 3 1 2 3 null null null null null null false 3 2 0 3 null null null null null null 2 1 null null null null null null 2.0 false false 1 Manchester United MUN 201617 20161702 true 2 0 2 3 null null null null null null false 6 4 3 3 null null null null null null 4 2 null null null null null null 2.0 false false 1 Manchester United MUN 201617 20161703 false 1 0 1 3 null null null null null null false 9 5 3 6 null null null null null null 5 3 null null null null null null 1.667 false false 1 Manchester United MUN 201617 20161704 true 1 2 -1 0 null null null null null null false 9 4 3 6 null null null null null null 4 4 null null null null null null 1.0 false false 1 Manchester United MUN 201617 20161705 false 1 3 -2 0 null null null null null null false 9 2 3 6 null null null null null null 2 5 null null null null null null 0.4 false false 1 Manchester United MUN 201617 20161706 true 4 1 3 3 null null null null null null false 9 3 6 3 null null null null null null 3 5 null null null null null null 0.6 false false 1 Manchester United MUN 201617 20161707 true 1 1 0 1 null null null null null null false 7 1 4 3 null null null null null null 1 5 null null null null null null 0.2 false false 1 Manchester United MUN 201617 20161708 false 0 0 0 1 null null null null null null false 5 0 4 1 null null null null null null 0 5 null null null null null null 0.0 false false 1 Manchester United MUN 201617 20161709 false 0 4 -4 0 null null null null null null false 5 -3 4 1 null null null null null null -3 5 null null null null null null -0.6 false false 1 Manchester United MUN 201617 20161710 true 0 0 0 1 null null null null null null false 6 -1 5 1 null null null null null null -1 5 null null null null null null -0.2 false false 1 Manchester United MUN 201617 20161711 false 3 1 2 3 null null null null null null false 6 -2 2 4 null null null null null null -2 5 null null null null null null -0.4 false false 1 Manchester United MUN 201617 20161712 true 1 1 0 1 null null null null null null false 6 -2 2 4 null null null null null null -2 5 null null null null null null -0.4 false false 1 Manchester United MUN 201617 20161713 true 1 1 0 1 null null null null null null false 6 -2 3 3 null null null null null null -2 5 null null null null null null -0.4 false false 1 Manchester United MUN 201617 20161714 false 1 1 0 1 null null null null null null false 7 2 3 4 null null null null null null 2 5 null null null null null null 0.4 false false 1 Manchester United MUN 201617 20161715 true 1 0 1 3 null null null null null null false 9 3 5 4 null null null null null null 3 5 null null null null null null 0.6 false false 1 Manchester United MUN 201617 20161716 false 2 1 1 3 null null null null null null false 9 2 5 4 null null null null null null 2 5 null null null null null null 0.4 false false 1 Manchester United MUN 201617 20161717 false 2 0 2 3 null null null null null null false 11 4 4 7 null null null null null null 4 5 null null null null null null 0.8 false false 1 Manchester United MUN 201617 20161718 true 3 1 2 3 null null null null null null false 13 6 6 7 null null null nul

#Player Features

In [0]:
df = spark.table("fpl_silver_dev.gameweek_stats")
df.printSchema()

root
 |-- fixture_key: string (nullable = true)
 |-- player_id: integer (nullable = true)
 |-- assists: integer (nullable = true)
 |-- bonus: integer (nullable = true)
 |-- bps: integer (nullable = true)
 |-- clean_sheets: integer (nullable = true)
 |-- clearances_blocks_interceptions: integer (nullable = true)
 |-- creativity: double (nullable = true)
 |-- defensive_contribution: integer (nullable = true)
 |-- expected_assists: double (nullable = true)
 |-- expected_goal_involvements: double (nullable = true)
 |-- expected_goals: double (nullable = true)
 |-- expected_goals_conceded: double (nullable = true)
 |-- fixture: integer (nullable = true)
 |-- goals_conceded: integer (nullable = true)
 |-- goals_scored: integer (nullable = true)
 |-- ict_index: double (nullable = true)
 |-- influence: double (nullable = true)
 |-- minutes: integer (nullable = true)
 |-- own_goals: integer (nullable = true)
 |-- penalties_missed: integer (nullable = true)
 |-- penalties_saved: integer (nullabl

In [0]:
df = spark.table("fpl_bronze_dev.game_config_scoring_25_26")

display(df)

scoring last_updated List(3, 1, 0, List(4, 0, 4, 1), 0, 0, List(2, 2, 0, 2), 0, 0, 0, 0, List(-1, 0, -1, 0), List(6, 4, 10, 5), 0, 0, 2, List(0, 0, 0, 0), List(0, 0, 0, 0), List(0, 0, 0, 0), 0, List(0, 0, 0, 0), List(0, 0, 0, 0), List(0, 0, 0, 0), -2, -2, 5, 0, -3, 1, 1, 1, 0, 0, 0, -1) 2025-10-26T14:13:56.031Z

In [0]:
#Prepare rolling window
player_rolling_window = Window.partitionBy("player_id", "season_key", "team_key").orderBy("gameweek_key").rowsBetween(-rolling_window_size + 1, 0)

#Calculate rolling player stats (including new FPL point features)
player_rolling_exprs = {
    "rolling_expected_goals": F.sum("expected_goals").over(player_rolling_window),
    "rolling_expected_assists": F.sum("expected_assists").over(player_rolling_window),
    "rolling_expected_goal_involvements": F.sum("expected_goal_involvements").over(player_rolling_window),
    "rolling_goals_scored": F.sum("goals_scored").over(player_rolling_window),
    "rolling_assists": F.sum("assists").over(player_rolling_window),
    "rolling_total_points": F.sum("total_points").over(player_rolling_window),
    "rolling_minutes": F.sum("minutes").over(player_rolling_window),
    "rolling_clean_sheets": F.sum("clean_sheets").over(player_rolling_window),
    "rolling_bps": F.sum("bps").over(player_rolling_window),
    "rolling_ict_index": F.sum("ict_index").over(player_rolling_window),
    "rolling_influence": F.sum("influence").over(player_rolling_window),
    "rolling_creativity": F.sum("creativity").over(player_rolling_window),
    "rolling_threat": F.sum("threat").over(player_rolling_window),
    "rolling_defensive_contribution": F.sum("defensive_contribution").over(player_rolling_window),
    "rolling_clearances_blocks_interceptions": F.sum("clearances_blocks_interceptions").over(player_rolling_window),
    "rolling_bonus": F.sum("bonus").over(player_rolling_window),
    # Position-specific: saves only for GK
    "rolling_saves": F.sum(F.when(F.col("position_key") == 1, F.col("saves")).otherwise(None)).over(player_rolling_window),
    "rolling_games_played": F.count("fixture_key").over(player_rolling_window),
    # Rolling FPL rule-based points
    "rolling_minutes_points": F.sum("minutes_points").over(player_rolling_window),
    "rolling_assist_points": F.sum("assist_points").over(player_rolling_window),
    "rolling_goal_points": F.sum("goal_points").over(player_rolling_window),
    "rolling_clean_sheet_points": F.sum("clean_sheet_points").over(player_rolling_window),
    "rolling_defensive_contribution_points": F.sum("defensive_contribution_points").over(player_rolling_window),
    "rolling_penalty_miss_points": F.sum("penalty_miss_points").over(player_rolling_window),
    "rolling_goals_conceded_points": F.sum("goals_conceded_points").over(player_rolling_window),
    "rolling_yellow_card_points": F.sum("yellow_card_points").over(player_rolling_window),
    "rolling_red_card_points": F.sum("red_card_points").over(player_rolling_window),
    "rolling_own_goal_points": F.sum("own_goal_points").over(player_rolling_window)
}

player_features_df = stats_df.withColumns(player_rolling_exprs)

#Calculate rolling averages to 3 decimal places
player_avg_exprs = {
    f"avg_{k[8:]}": F.round(
        F.when(
            F.col("rolling_games_played") != 0,
            F.col(k) / F.col("rolling_games_played")
        ).otherwise(None),
        3
    )
    for k in player_rolling_exprs if k != "rolling_games_played"
}
player_features_df = player_features_df.withColumns(player_avg_exprs)

# Join with team_features for contextual strength and match_points
pf = player_features_df.alias("pf")
tf = team_features_df.alias("tf")

team_strength_cols = [
    F.col("team_key").alias("_team_key"), F.col("season_key").alias("team_season_key"), F.col("gameweek_key").alias("team_gamweek_key"),
    "rolling_points", "rolling_team_expected_goals",
    "rolling_expected_goals_against", "rolling_goal_difference",
    "avg_team_expected_goals", "avg_team_expected_assists", "avg_team_expected_goal_involvements",
    "avg_expected_goals_against", "avg_expected_assists_against", "avg_expected_goal_involvements_against",
    "avg_goal_difference", "match_points"
]

tf = tf.select(*team_strength_cols)

pf = pf.join(
    tf,
    (pf["team_key"] == tf["_team_key"]) &
    (pf["season_key"] == tf["team_season_key"]) &
    (pf["gameweek_key"] == tf["team_gamweek_key"]),
    how="left"
).drop("_team_key", "team_season_key", "team_gamweek_key")

# Join opponent team strength features
tf_opp = team_features_df.alias("tf_opp")
opponent_team_strength_cols = [
    F.col("team_key").alias("_opponent_team_key"),
    F.col("season_key").alias("opponent_season_key"),
    F.col("gameweek_key").alias("opponent_gameweek_key"),
    F.col("rolling_points").alias("opponent_rolling_points"),
    F.col("rolling_team_expected_goals").alias("opponent_rolling_team_expected_goals"),
    F.col("rolling_goal_diff").alias("opponent_rolling_goal_diff"),
    F.col("rolling_expected_goals_against").alias("opponent_rolling_expected_goals_against"),
    F.col("rolling_goal_difference").alias("opponent_rolling_goal_difference"),
    F.col("avg_team_expected_goals").alias("opponent_avg_team_expected_goals"),
    F.col("avg_team_expected_assists").alias("opponent_avg_team_expected_assists"),
    F.col("avg_team_expected_goal_involvements").alias("opponent_avg_team_expected_goal_involvements"),
    F.col("avg_expected_goals_against").alias("opponent_avg_expected_goals_against"),
    F.col("avg_expected_assists_against").alias("opponent_avg_expected_assists_against"),
    F.col("avg_expected_goal_involvements_against").alias("opponent_avg_expected_goal_involvements_against"),
    F.col("avg_goal_difference").alias("opponent_avg_goal_difference")
]

tf_opp = team_features_df.select(*opponent_team_strength_cols)

pf = pf.join(
    tf_opp,
    (pf["opponent_team_key"] == tf_opp["_opponent_team_key"]) &
    (pf["season_key"] == tf_opp["opponent_season_key"]) &
    (pf["gameweek_key"] == tf_opp["opponent_gameweek_key"]),
    how="left"
).drop("_opponent_team_key", "opponent_season_key", "opponent_gameweek_key")

#For GK/DEF/MID, add team defensive rolling stats
player_features_df = pf.withColumns({
    "team_rolling_goals_conceded": F.when(F.col("position_key").isin([1,2,3]), F.col("rolling_expected_goals_against")).otherwise(None),
    "team_rolling_goal_difference": F.when(F.col("position_key").isin([1,2,3]), F.col("rolling_goal_difference")).otherwise(None)
})

#Add ratios of team share
player_features_df = player_features_df.withColumns({
    "player_share_of_team_xG": F.round(
        F.when(
            F.col("rolling_team_expected_goals") != 0,
            F.col("rolling_expected_goals") / F.col("rolling_team_expected_goals")
        ).otherwise(None),
        3
    ),
    "player_share_of_team_points": F.round(
        F.when(
            F.col("rolling_points") != 0,
            F.col("rolling_total_points") / F.col("rolling_points")
        ).otherwise(None),
        3
    )
})

#Select final columns, including raw stats from stats_df and match_points from team_features
raw_stats_cols = [
    "fixture_key", "player_id", "player_key", "player_season_key", "team_key", "season_key", "gameweek_key", "position_key", "opponent_team_key", "was_home", "exp_stats_available"#,
    #"assists", "bonus", "bps", "clean_sheets", "clearances_blocks_interceptions", "creativity", "defensive_contribution", "expected_assists", "expected_goal_involvements",
    #"expected_goals", "expected_goals_conceded", "goals_conceded", "goals_scored", "ict_index", "influence", "minutes", "own_goals", "penalties_missed", "penalties_saved",
    #"recoveries", "red_cards", "saves", "threat", "total_points", "value", "def_con_available", "team_score", "opponent_score", "player_fixture_key",
    #"minutes_points", "assist_points", "goal_points", "clean_sheet_points", "defensive_contribution_points", "penalty_miss_points", "goals_conceded_points",
    #"yellow_card_points", "red_card_points", "own_goal_points"
]

final_cols = [
    *raw_stats_cols,
    # Rolling stats
    *list(player_rolling_exprs.keys()),
    # Rolling averages
    *list(player_avg_exprs.keys()),
    # Team/contextual features
    "rolling_points", "rolling_team_expected_goals", "rolling_expected_goals_against", "rolling_goal_difference",
    "avg_team_expected_goals", "avg_team_expected_assists", "avg_team_expected_goal_involvements",
    "avg_expected_goals_against", "avg_expected_assists_against", "avg_expected_goal_involvements_against",
    "avg_goal_difference",
    "match_points",
    "team_rolling_goals_conceded", "team_rolling_goal_difference",
    "player_share_of_team_xG", "player_share_of_team_points",
    # Opponent team strength features
    "opponent_rolling_points", "opponent_rolling_team_expected_goals",
    "opponent_rolling_expected_goals_against", "opponent_rolling_goal_difference",
    "opponent_avg_team_expected_goals", "opponent_avg_team_expected_assists", "opponent_avg_team_expected_goal_involvements",
    "opponent_avg_expected_goals_against", "opponent_avg_expected_assists_against", "opponent_avg_expected_goal_involvements_against",
    "opponent_avg_goal_difference"
]

player_features_df = player_features_df.select(*final_cols)

#Write to feature table
write_to_table(
    df=player_features_df,
    table_name=f"{feature_schema}.player_features",
    mode="overwrite"
)